# Assignment 3
## 

Use AlexNet and write report about it.

Data: Cat & Dog

You should use keras library to classify cat and dog. 

In [9]:
from mat4py import loadmat
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical
from keras.applications import imagenet_utils
from keras.preprocessing.image import img_to_array, array_to_img


In [2]:
# Load data
data = loadmat('CatDog.mat')
data

{'X': [[-1.847107438016522,
   -43.84710743801652,
   -68.84710743801652,
   -17.847107438016522,
   116.15289256198348,
   -4.847107438016522,
   117.15289256198348,
   67.15289256198348,
   29.152892561983478,
   -74.84710743801652,
   1.152892561983478,
   -82.84710743801652,
   -100.84710743801652,
   -28.847107438016522,
   148.1528925619835,
   147.1528925619835,
   2.152892561983478,
   -39.84710743801652,
   30.152892561983478,
   -51.84710743801652,
   -70.84710743801652,
   -66.84710743801652,
   66.15289256198348,
   -3.847107438016522,
   8.152892561983478,
   -64.84710743801652,
   -53.84710743801652,
   -3.847107438016522,
   126.15289256198348,
   -101.84710743801652,
   -0.847107438016522,
   -97.84710743801652,
   88.15289256198348,
   -59.84710743801652,
   70.15289256198348,
   -83.84710743801652,
   -72.84710743801652,
   47.15289256198348,
   53.15289256198348,
   47.15289256198348,
   -50.84710743801652,
   -90.84710743801652,
   -8.847107438016522,
   148.1528925

In [3]:
# available in the loaded data
print(data.keys())

dict_keys(['X', 'G', 'nx', 'ny'])


In [4]:
X_length = len(data['X'])
print("length of X:", X_length)
G_length = len(data['G'])
print("length of G:", G_length)


length of X: 4096
length of G: 242


In [5]:
# Reshape X to represent images
X_reshaped = np.array(data['X']).reshape(-1, 64, 64, 1)  # Assuming the images are grayscale


In [6]:
# Convert labels to numpy array
y = np.array(data['G'])

In [10]:
y.value_counts().plot.bar()

AttributeError: 'numpy.ndarray' object has no attribute 'value_counts'

In [9]:
# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_reshaped, y, test_size=0.2, random_state=42)

In [10]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout

# Define the modified AlexNet model architecture
model = Sequential()

# Convolutional layers
model.add(Conv2D(96, kernel_size=(11, 11), strides=(4, 4), activation='relu', input_shape=(64, 64, 1)))
model.add(MaxPooling2D(pool_size=(3, 3), strides=(2, 2)))
model.add(Conv2D(256, kernel_size=(5, 5), padding='same', activation='relu'))
model.add(Conv2D(384, kernel_size=(3, 3), padding='same', activation='relu'))
model.add(Conv2D(384, kernel_size=(3, 3), padding='same', activation='relu'))
model.add(Conv2D(256, kernel_size=(3, 3), padding='same', activation='relu'))
model.add(MaxPooling2D(pool_size=(3, 3), strides=(2, 2)))

# Dense layers
model.add(Flatten())
model.add(Dense(4096, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(4096, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))  # Output layer, binary classification

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Train the model
history = model.fit(X_train, y_train, batch_size=128, epochs=10, validation_split=0.1)

# Evaluate the model on the test set
accuracy = model.evaluate(X_test, y_test)
print("Test Accuracy:", accuracy[1])


Epoch 1/10


2/2 [==============================] - 3s 812ms/step - loss: 15.9739 - accuracy: 0.4913 - val_loss: 10.7549 - val_accuracy: 0.4500
Epoch 2/10
2/2 [==============================] - 1s 525ms/step - loss: 6.8558 - accuracy: 0.5145 - val_loss: 1.2566 - val_accuracy: 0.5500
Epoch 3/10
2/2 [==============================] - 1s 524ms/step - loss: 1.2571 - accuracy: 0.4682 - val_loss: 0.6877 - val_accuracy: 0.5500
Epoch 4/10
2/2 [==============================] - 1s 537ms/step - loss: 0.6993 - accuracy: 0.4509 - val_loss: 0.7368 - val_accuracy: 0.4500
Epoch 5/10
2/2 [==============================] - 1s 514ms/step - loss: 0.7069 - accuracy: 0.5260 - val_loss: 0.8566 - val_accuracy: 0.4500
Epoch 6/10
2/2 [==============================] - 1s 523ms/step - loss: 0.7602 - accuracy: 0.5145 - val_loss: 0.6911 - val_accuracy: 0.5500
Epoch 7/10
2/2 [==============================] - 1s 522ms/step - loss: 0.6940 - accuracy: 0.4855 - val_loss: 0.6907 - val_accuracy: 0.5500
Epoch 8/10
2/2 [

In [11]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator

# Data augmentation
datagen = ImageDataGenerator(
    rotation_range=20,
    width_shift_range=0.2,
    height_shift_range=0.2,
    horizontal_flip=True,
    vertical_flip=True,
    zoom_range=0.2,
    fill_mode='nearest')

# Normalizing the data
X_train_normalized = X_train / 255.0
X_test_normalized = X_test / 255.0

# Fit the augmentation on the training data
datagen.fit(X_train_normalized)

# Training the model with augmented data
history = model.fit(datagen.flow(X_train_normalized, y_train, batch_size=128),
                    epochs=10, validation_data=(X_test_normalized, y_test))

# Evaluate the model on the test set
accuracy = model.evaluate(X_test_normalized, y_test)
print("Test Accuracy:", accuracy[1])


Epoch 1/10
2/2 [==============================] - 3s 686ms/step - loss: 0.6939 - accuracy: 0.4922 - val_loss: 0.6921 - val_accuracy: 0.5306
Epoch 2/10
2/2 [==============================] - 2s 651ms/step - loss: 0.6939 - accuracy: 0.4922 - val_loss: 0.6923 - val_accuracy: 0.5306
Epoch 3/10
2/2 [==============================] - 2s 756ms/step - loss: 0.6937 - accuracy: 0.4922 - val_loss: 0.6924 - val_accuracy: 0.5306
Epoch 4/10
2/2 [==============================] - 2s 691ms/step - loss: 0.6934 - accuracy: 0.4922 - val_loss: 0.6926 - val_accuracy: 0.5306
Epoch 5/10
2/2 [==============================] - 2s 1s/step - loss: 0.6933 - accuracy: 0.4922 - val_loss: 0.6929 - val_accuracy: 0.5306
Epoch 6/10
2/2 [==============================] - 1s 850ms/step - loss: 0.6934 - accuracy: 0.4922 - val_loss: 0.6932 - val_accuracy: 0.4694
Epoch 7/10
2/2 [==============================] - 2s 1s/step - loss: 0.6932 - accuracy: 0.4715 - val_loss: 0.6935 - val_accuracy: 0.4694
Epoch 8/10
2/2 [==========